In [ ]:
# Prepare packages on remote machine
# !pip install datasets
# !pip install seqeval
!pip install transformers
!pip install bertviz

     |████████████████████████████████| 2.3MB 24.1MB/s 
     |████████████████████████████████| 901kB 40.0MB/s 
     |████████████████████████████████| 3.3MB 43.1MB/s 
     |████████████████████████████████| 153kB 29.8MB/s 
     |████████████████████████████████| 1.2MB 35.4MB/s 
     |████████████████████████████████| 133kB 51.6MB/s 
     |████████████████████████████████| 7.6MB 33.2MB/s 
     |████████████████████████████████| 81kB 733kB/s 
ERROR: botocore 1.20.84 has requirement urllib3<1.27,>=1.25.4, but you'll have urllib3 1.24.3 which is incompatible.


In [ ]:
%%time
from transformers import AutoModel
import torch.nn as nn
from transformers.modeling_outputs import TokenClassifierOutput

class prestoBERT(nn.Module):
    def __init__(self, num_labels):
        super(prestoBERT, self).__init__()
        self.num_labels = num_labels

        self.bert = AutoModel.from_pretrained('KB/bert-base-swedish-cased', num_labels=len(unique_tags))
        self.dropout = nn.Dropout(self.bert.config.hidden_dropout_prob)
        self.classifier = nn.Linear(self.bert.config.hidden_size, self.num_labels)

    def forward(
        self,
        input_ids=None,
        attention_mask=None,
        token_type_ids=None,
        position_ids=None,
        head_mask=None,
        inputs_embeds=None,
        labels=None,
        output_attentions=None,
        output_hidden_states=None,
        return_dict=None,
    ):

        return_dict = return_dict if return_dict is not None else self.bert.config.use_return_dict

        outputs = self.bert(
            input_ids,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
            position_ids=position_ids,
            head_mask=head_mask,
            inputs_embeds=inputs_embeds,
            output_attentions=output_attentions,
            output_hidden_states=output_hidden_states,
            return_dict=return_dict,
        )

        sequence_output = outputs[0]

        sequence_output = self.dropout(sequence_output)
        logits = self.classifier(sequence_output)

        loss = None
        if labels is not None:
            # print("Labels not None")
            loss_fct = nn.CrossEntropyLoss()
            # Disregard the loss of inactive parts 
            if attention_mask is not None:
                active_loss = attention_mask.view(-1) == 1
                active_logits = logits.view(-1, self.num_labels)
                active_labels = torch.where(
                    active_loss, labels.view(-1), torch.tensor(loss_fct.ignore_index).type_as(labels)
                )
                loss = loss_fct(active_logits, active_labels)
            else:
                loss = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))

        if not return_dict:
            output = (logits,) + outputs[2:]
            return ((loss,) + output) if loss is not None else output

        return TokenClassifierOutput(
            loss=loss,
            logits=logits,
            hidden_states=outputs.hidden_states,
            attentions=outputs.attentions,
        )

CPU times: user 1.93 s, sys: 405 ms, total: 2.34 s
Wall time: 5.47 s


In [ ]:
# from sklearn.metrics import accuracy_score, precision_recall_fscore_support
# from datasets import ClassLabel, load_dataset, load_metric

# metric = load_metric("seqeval")

# def compute_metrics(p):
#     label_list = list(unique_tags)
#     predictions, labels = p
#     predictions = np.argmax(predictions, axis=2)

#     # Remove ignored index (special tokens)
#     true_predictions = [
#         [label_list[p] for (p, l) in zip(prediction, label) if l != -100]
#         for prediction, label in zip(predictions, labels)
#     ]
#     true_labels = [
#         [label_list[l] for (p, l) in zip(prediction, label) if l != -100]
#         for prediction, label in zip(predictions, labels)
#     ]

#     results = metric.compute(predictions=true_predictions, references=true_labels)
#     return {
#         "precision": results["overall_precision"],
#         "recall": results["overall_recall"],
#         "f1": results["overall_f1"],
#         "accuracy": results["overall_accuracy"],
#     }

# def model_init(num_labels):
#     return prestoBERT(num_labels=num_labels)

In [ ]:
# Load fine-tuned model
from bertviz import head_view, model_view
from transformers import AutoTokenizer
import torch

unique_tags = ['EMPTY', 'PERIOD', 'COMMA', 'QUESTION']
model = prestoBERT(4)
model.load_state_dict(torch.load('drive/MyDrive/master-thesis/pytorch_model.bin'))
tokenizer = AutoTokenizer.from_pretrained('KB/bert-base-swedish-cased')

Some weights of the model checkpoint at KB/bert-base-swedish-cased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.bias', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
sentence = "bild lars alexi uppväxt vid rälsen han går bort till mjölkdisken och tar en annan sorts ost och två liter mjölk"
# sentence = "en typisk mening består av en del ord till exempel substantiv och dylikt imorgon är det dags för finalen i fotbolls-VM men få är lika nyfikna som bert karlsson"
# sentence = "uppland läns landsting beslutade idag trots omständligheterna att bromma fotbollsklubb ej längre har tillstånd att bedriva verksamheten dagens agenda har två huvudsakliga punkter först och främst"
# sentence = "Emedan enligt det mellan parterna träffade avtal Pettersson och Jonsson skolat leverera det försälda virket fritt å banvagn vid Rosenfors och Mörlunda stationer samt de icke ens påstått att Lundin vägrat mottaga eller eljest gjort sig skyldig till dröjsmål med mottagandet av virke som blivit till honom avlämnat i vidare mån än att Lundin avvisat den av Pettersson och Jonsson den 7 september 1912 från Rosenfors station till Lundin avsända vagnslast virke men i målet vore upplyst att sistnämnda virkeslast icke varit av leveransgill beskaffenhet och Lundin förty varit berättigad att på sätt skett avvisa densamma ty och som Pettersson och Jonsson icke styrkt att Lundin i avseende å virkesleveranser som Pettersson och Jonsson stått i begrepp att fullgöra vidtagit någon åtgärd på grund varav de skäligen kunnat befara att därest leveranserna utfördes godset ej komme att av Lundin mottagas samt vid sådant förhållande faran för ifrågakomna i staplar upplagda virke ej kunnat på sätt Pettersson och Jonsson förmenade före dess avlämnande å Lundin övergå alltså och på i övrigt av HR n anförda skäl prövade HovRn rättvist fastställa det slut HRns utslag innehölle".lower()
# sentence = "aldrig oavsett vad igen"

# sentence = "Jorden, som vändes upp av plogen, låg svartbrun och sken av fukt och fetma, och han, som plöjde, gick och gladde sig åt att snart få så råg där. Han tänkte för sig själv: \"Hur kan det komma sig, att jag stundom gör mig så svåra bekymmer och tycker, att det är tungt att leva? Kan det behövas något mer än solsken och vackert väder för att vara säll som ett Guds barn i himmelen?\""
# sentence = "Enligt Stefan Östlund kan avancemanget på rankingen till viss del förklaras av nyheter i hur bedömningen går till. Men den högre placeringen är också ett resultat av att KTH har ett mer fokuserat sätt att arbeta med rankningar, betonar han. Inom flera hållbarhetsmål rankas KTH bland världens 20 främsta: Genomförande och globalt partnerskap (plats 7) Bekämpa klimatförändringarna (plats 7) och Hållbara städer och samhällen (plats 20)."
sentence = "Vi är verkligen glada över placeringen. Den speglar KTH:s medvetenhet i frågor kring hållbar utveckling, liksom en stark forskning och ett omfattande samarbete med både industri och offentliga organisationer, säger han."
sentence = "KTH-forskarna har tagit fram en ny metod för att förkolna biomassan vid betydligt lägre temperaturer. De omvandlar lignosulfonat, en biprodukt från trämassa, till kolflingor genom att värma upp det i vatten i en mikrovågsugn. Vattnet hettas upp till 240 grader Celsius och vidhåller 240 grader i två timmar."
sentence = "KTH-forskarna har tagit fram en ny metod för att förkolna biomassan vid betydligt lägre temperaturer. De omvandlar lignosulfonat, en biprodukt från trämassa, till kolflingor genom att värma upp det i vatten i en mikrovågsugn. Vattnet hettas upp till 240 grader Celsius och vidhåller 240 grader i två timmar. Efter oxideringsprocessen bryts kolflingorna upp i små beståndsdelar, små kolbitar om 10 till 80 nanometer i diameter, som sedan blandas med cellulosagummit och behandla med UV-ljus för att forma hydrogelen. Detta är en enkel, hållbar lösning. Det fungerar lika bra, om inte bättre, än liknande hydrogelbaserade reningstekniker som används idag, säger Minna Hakkarainen."
sentence = "Vattnet hettas upp till 240 grader Celsius och vidhåller 240 grader i två timmar."

# Clean up 
sentence = sentence.lower()
sentence = sentence.replace("#", "")
sentence = sentence.replace(" - ", ", ")
sentence = sentence.replace("-\n", "")
sentence = sentence.replace(";", ":")
sentence = sentence.replace("!", ".")
sentence = sentence.replace("\"", ",")
sentence = sentence.replace(":", " :")
sentence = sentence.replace(",", "")
sentence = sentence.replace(".", "")
sentence = sentence.replace("?", "")
print(sentence)

inputs = tokenizer.encode_plus(sentence, return_tensors='pt', truncation=True, padding=True, max_length=None)
input_ids = inputs['input_ids']
token_type_ids = inputs['token_type_ids']
attention = model(input_ids, token_type_ids=token_type_ids, output_attentions=True)[-1]
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
# print(input_id_list)
full_tokens = tokens
tokens = tokens[1:-1]
print("nb tokens:", len(tokens))
print(tokens)
# end_of_word_indices = []
# for i in range(1, len(tokens)):
#     if "##" not in tokens[i]:
#         end_of_word_indices.append(i-1)
# end_of_word_indices.append(len(tokens)-1)
start_of_word_indices = [i for i in range(len(tokens)) if "##" not in tokens[i]]
# bad_indices = [i for i in range(len(tokens)) if "##" in tokens[i]]
# print(end_of_word_indices)
# print(start_of_word_indices)

vattnet hettas upp till 240 grader celsius och vidhåller 240 grader i två timmar
nb tokens: 18
['vattnet', 'hetta', '##s', 'upp', 'till', '240', 'grader', 'cel', '##si', '##us', 'och', 'vid', '##håller', '240', 'grader', 'i', 'två', 'timmar']


In [ ]:
import tensorflow as tf
import numpy as np

predictions = model.forward(input_ids).logits.detach()
pred_per_word = predictions.detach()[0][1:-1]
predictions = np.argmax(predictions, axis=2).detach().ravel()[1:-1] # remove CLS and SEP
# print(predictions)

# label_list = ['EMPTY', 'PERIOD', 'COMMA', 'QUESTION']
label_list = ['PERIOD', 'EMPTY', 'COMMA', 'QUESTION']

predictions = [label_list[int(p)] for p in predictions]

print(label_list)
# print(pred_per_word[i].detach().numpy())
for i in range(len(tokens)):
    print(tokens[i], "\t", '\t'.join([str(round(val, 1)) for val in pred_per_word[i].detach().numpy()]))

# Doing this less verbose crashes Colab...
comma_enc = tokenizer.encode(",")
comma_enc = [comma_enc[1]]
comma_enc = torch.tensor(comma_enc)
question_enc = tokenizer.encode("?")
question_enc = [question_enc[1]]
question_enc = torch.tensor(question_enc)
period_enc = tokenizer.encode(".")
period_enc = [period_enc[1]]
period_enc = torch.tensor(period_enc)
output_ids = input_ids.ravel()[1:-1]
# print(predictions)
# print(output_ids)

### START prediction
# Merge words back together
words = []
for token in tokens:
    if "##" not in token:
        words.append(token)
    else:
                    words[-1] += token.replace("##", "") # build on last wor d
# Get START predictions
predictions = [predictions[i] for i in start_of_word_indices]
# print(predictions)
for i in range(len(words)):
            if predictions[i] == "COMMA": 
                                            words[i] += ","
            elif predictions[i] == "QUESTION":
                words[i] += "?"
            elif predictions[i] == "PERIOD":
                            words[i] += "."

output = ' '.join(words)
output = output.replace(" : ", ": ")
output = output.replace("( ", "(")
output = output.replace(" )", ")")
print(output)

['PERIOD', 'EMPTY', 'COMMA', 'QUESTION']
vattnet 	 -3.5	8.1	-2.5	-3.2
hetta 	 -2.1	8.2	-2.8	-2.6
##s 	 -2.7	8.6	-2.9	-3.1
upp 	 -3.2	8.1	-2.2	-3.7
till 	 -3.2	6.7	-0.4	-3.0
240 	 -2.9	7.9	-2.5	-2.8
grader 	 -2.9	7.2	-1.1	-3.4
cel 	 -2.3	4.1	0.8	-3.7
##si 	 -2.5	4.4	0.9	-3.8
##us 	 -2.3	4.0	1.2	-4.0
och 	 -3.2	8.6	-2.8	-2.7
vid 	 -2.4	8.3	-2.9	-3.3
##håller 	 -2.4	7.7	-2.7	-3.4
240 	 -2.5	8.5	-2.4	-3.3
grader 	 -2.5	7.5	-1.4	-3.5
i 	 -3.1	8.1	-2.5	-2.7
två 	 -2.7	8.3	-2.8	-2.4
timmar 	 8.2	-2.5	-3.0	-3.0
vattnet hettas upp till 240 grader celsius och vidhåller 240 grader i två timmar.


In [ ]:
model_view(attention, full_tokens)

<IPython.core.display.Javascript object>

In [ ]:
head_view(attention, full_tokens)

<IPython.core.display.Javascript object>